# IMAO - Codes correcteurs

## Matrices des codes

In [1]:
%display latex

In [2]:
F2=FiniteField(2)

Matrices G

In [3]:
def get_G1():
    G1=matrix(F2,9,8)
    for i in range(8):
        G1[i,i]=1
    for i in range(8):
        G1[8,i]=1
    return G1

In [4]:
G1=get_G1();G1

[1 0 0 0 0 0 0 0]
[0 1 0 0 0 0 0 0]
[0 0 1 0 0 0 0 0]
[0 0 0 1 0 0 0 0]
[0 0 0 0 1 0 0 0]
[0 0 0 0 0 1 0 0]
[0 0 0 0 0 0 1 0]
[0 0 0 0 0 0 0 1]
[1 1 1 1 1 1 1 1]

In [5]:
G2=matrix(F2,3,1,[1,1,1]);G2

[1]
[1]
[1]

In [6]:
G3=matrix(F2,4,2,[1,0,0,1,1,0,1,1]);G3

[1 0]
[0 1]
[1 0]
[1 1]

In [7]:
G4=matrix(F2,7,4,[1,0,0,0,0,1,0,0,0,0,1,0,0,0,0,1,1,1,0,1,1,0,1,1,0,1,1,1]);G4

[1 0 0 0]
[0 1 0 0]
[0 0 1 0]
[0 0 0 1]
[1 1 0 1]
[1 0 1 1]
[0 1 1 1]

## Image

In [8]:
def image(G):
    (n,k)=G.dimensions()
    U=VectorSpace(F2,k)
    return [G*m for m in U]

In [9]:
len(image(G1))

256

In [10]:
image(G2)

[(0, 0, 0), (1, 1, 1)]

In [11]:
image(G3)

[(0, 0, 0, 0), (1, 0, 1, 1), (0, 1, 0, 1), (1, 1, 1, 0)]

In [12]:
image(G4)

[(0, 0, 0, 0, 0, 0, 0),
 (1, 0, 0, 0, 1, 1, 0),
 (0, 1, 0, 0, 1, 0, 1),
 (1, 1, 0, 0, 0, 1, 1),
 (0, 0, 1, 0, 0, 1, 1),
 (1, 0, 1, 0, 1, 0, 1),
 (0, 1, 1, 0, 1, 1, 0),
 (1, 1, 1, 0, 0, 0, 0),
 (0, 0, 0, 1, 1, 1, 1),
 (1, 0, 0, 1, 0, 0, 1),
 (0, 1, 0, 1, 0, 1, 0),
 (1, 1, 0, 1, 1, 0, 0),
 (0, 0, 1, 1, 1, 0, 0),
 (1, 0, 1, 1, 0, 1, 0),
 (0, 1, 1, 1, 0, 0, 1),
 (1, 1, 1, 1, 1, 1, 1)]

## Distance

In [13]:
def poids_Hamming(x):
    d=0
    for i in range(len(x)):
        if x[i]!=0:
            d=d+1
    return d

In [14]:
def distance(G):
    C=image(G)
    d=Infinity
    for x in C:
        if x!=0:
            d=min(d,poids_Hamming(x))
    return d

In [15]:
distance(G1)

2

In [16]:
distance(G2)

3

In [17]:
distance(G3)

2

In [18]:
distance(G4)

3

## MDS ?

In [19]:
def est_mds(G):
    (n,k)=G.dimensions()
    d=distance(G)
    return d==n-k+1

In [20]:
est_mds(G1)

True

In [21]:
est_mds(G2)

True

In [22]:
est_mds(G3)

False

In [23]:
est_mds(G4)

False

## Systematique

In [24]:
def est_systematique(G):
    (n,k)=G.dimensions()
    return G.submatrix(0,0,k,k).is_one()

In [25]:
est_systematique(G1)

True

In [26]:
est_systematique(G2)

True

In [27]:
est_systematique(G3)

True

In [28]:
est_systematique(G4)

True

## Matrice de contrôle

In [29]:
def matrice_controle(G):
    (n,k)=G.dimensions()
    GG=G.submatrix(k,0,n-k,k)
    H=matrix(F2,n-k,n)
    H.set_block(0,0,GG)
    H.set_block(0,k,identity_matrix(F2,n-k))
    return H

In [30]:
matrice_controle(G1)


[1 1 1 1 1 1 1 1 1]

In [31]:
matrice_controle(G2)

[1 1 0]
[1 0 1]

In [32]:
matrice_controle(G3)

[1 0 1 0]
[1 1 0 1]

In [33]:
matrice_controle(G4)

[1 1 0 1 1 0 0]
[1 0 1 1 0 1 0]
[0 1 1 1 0 0 1]

## Table de décodage

In [34]:
def table_decodage(G):
    H=matrice_controle(G)
    (n,k)=G.dimensions()
    d=distance(G)
    table={}
    E=VectorSpace(F2,n)
    for e in E:
        s=H*e
        s.set_immutable() # Transfome le vecteur s en vecteur que l'on ne pourra plus modifier
        if s in table: # Une erreur est deja affecte au syndrome
            f=table[s] # On recupere l'erreur affecte
            if poids_Hamming(e)<poids_Hamming(f):
                # Si e a un poid de Hamming inferieur a celle presente dans la table
                # on met à jour l'erreur associée au syndrome e
                table[s]=e
        else:
            table[s]=e
    return table

In [35]:
table_decodage(G1)

{(0): (0, 0, 0, 0, 0, 0, 0, 0, 0), (1): (1, 0, 0, 0, 0, 0, 0, 0, 0)}

In [36]:
table_decodage(G2)

{(0, 0): (0, 0, 0), (1, 1): (1, 0, 0), (1, 0): (0, 1, 0), (0, 1): (0, 0, 1)}

In [37]:
table_decodage(G3)

{(0, 0): (0, 0, 0, 0),
 (1, 1): (1, 0, 0, 0),
 (0, 1): (0, 1, 0, 0),
 (1, 0): (0, 0, 1, 0)}

In [38]:
table_decodage(G4)

{(0, 0, 0): (0, 0, 0, 0, 0, 0, 0),
 (1, 1, 0): (1, 0, 0, 0, 0, 0, 0),
 (1, 0, 1): (0, 1, 0, 0, 0, 0, 0),
 (0, 1, 1): (0, 0, 1, 0, 0, 0, 0),
 (1, 1, 1): (0, 0, 0, 1, 0, 0, 0),
 (0, 0, 1): (0, 0, 0, 0, 0, 0, 1),
 (0, 1, 0): (0, 0, 0, 0, 0, 1, 0),
 (1, 0, 0): (0, 0, 0, 0, 1, 0, 0)}

## Décodage

In [39]:
def decode(G,m):
    m=vector(F2,m)
    (n,k)=G.dimensions()
    H=matrice_controle(G)
    d=distance(G)
    ec=(d-1)/2
    table=table_decodage(G)
    s=H*m
    s.set_immutable()
    if s==0:
        return m[:k]
    else:
        e=table[s]
        if poids_Hamming(e)<=ec:
            m=m+e
            return m[:k]
        print("Correction impossible")

In [40]:
decode(G1,[1,0,1,0,1,0,1,0,0])

(1, 0, 1, 0, 1, 0, 1, 0)

In [41]:
decode(G2,[1,0,1])

(1)

In [42]:
decode(G3,[1,1,0,0])

Correction impossible


In [43]:
decode(G4,[1,0,1,1,1,1,1])

(1, 1, 1, 1)